In [297]:
import sys
import numpy as np
import random
import subprocess
import pandas as pd
import string
import torch
import torch.nn as nn
import time
import math
import matplotlib.pyplot as plt
import matplotlib.ticker as ticker
from dna2vec.dna2vec.multi_k_model import MultiKModel
from collections import Counter, defaultdict

### Contaminant Genome Analysis Pipeline

In [325]:
# Constants for Simulation
READ_LENGTH = 90
LINE_LENGTH = 90
CONTAMINATION_RATE = 0.05

UNCONTAMINATED_HEADER_LINE = ">Uncontaminated Human Chr. 21, complete genome"
DEFAULT_HEADER = ">reads.fna"
CONTAMINANT_HEADER = ">Contaminated Genome"
OVERLAP_HEADER = ">Overlapped from Contaminant Genomes"
OVERLAP_OUTPUT_FILE = "overlap.fna"

# Constants for Bowtie2 alignment
BOWTIE_ALIGNMENTS_INPUT = "cont.sam"
BOWTIE_UNMAPPED_OUTPUT = "unmapped_alignments.txt"
TABLE_LEN = 13
UNMAPPED_STATUS_COL = 1
UNMAPPED_FLAG = 4
MAPPED_FLAG = 0
READ_COL = 9

# Constants for Overlap between Deep Learning Predictions and Sketching
RNN_THRESHOLD = 0.5
ALIGNMENT_VALIDATION_LIMIT = 1000

In [268]:
def parse_fasta(filename, read_length, limit=-1):
    reads = []
    read = ""
    n_char = "N"
    with open(filename, "r") as fa:
        read = ""
        for line in fa:
            if len(reads) == limit:
                return reads
            if line.startswith(">"):
                continue
            line = line.upper()
            end = min(read_length - len(read), len(line))
            offset = 0
            while offset+end < len(line):
                read += line[offset:offset+end]
                if n_char not in read:
                    reads.append(read)
                    if limit != -1 and len(reads) >= limit:
                        return reads
                offset += end
                end = read_length
                read = ""
            read += line[offset:-1]
            if len(read) == READ_LENGTH:
                if n_char not in read:
                    reads.append(read)
                    if limit != -1 and len(reads) >= limit:
                        return reads
                read = ""
        if read:
            if n_char not in read:
                reads.append(read)
    return reads

In [307]:
def write_fasta(filename, reads, header=None, label=DEFAULT_HEADER, limit=150, append=False):
    index = 0
    mode = "a" if append else "w"
    with open(filename, mode) as fw:
        if header:
            fw.write(header + "\n")
        start = 0
        for read in reads:
            offset = 0
            while offset + limit - start < len(read):
                fw.write(read[offset:offset+limit-start] + "\n")
                offset += limit-start
                index += 1
                if header:
                    fw.write(label + " read %d:\n"%(index))
                start = 0
            if start > 0 and limit - start < len(read):
                fw.write(read[:limit-start] + "\n")
                index += 1
                if header:
                    fw.write(label + " read %d:\n"%(index))
                offset, start = limit-start, 0
            fw.write(read[offset:])
            start += len(read)-offset

In [270]:
def contaminate(src_reads, contaminant):
    n_contaminants = int(CONTAMINATION_RATE * len(src_reads))
    print("introducing %d contaminants from contaminant %s"%(n_contaminants, contaminant))
    contaminant_reads = parse_fasta(contaminant, READ_LENGTH, n_contaminants)
    src_reads_copy = src_reads.copy()
    src_reads_copy.extend(contaminant_reads)
    return src_reads_copy

### Streamlined Simulation Pipeline

In [271]:
human_genome = parse_fasta("chr21.fa", READ_LENGTH)
print("%d reads extracted from source genome"%(len(human_genome)))
write_fasta(filename="humanChrom21.fna", 
            reads=human_genome, 
            header=UNCONTAMINATED_HEADER_LINE, 
            label=">human.fna",
            limit=LINE_LENGTH)

445378 reads extracted from source genome
writing to humanChrom21.fna


### Simulated Contamination Pipeline

In [272]:
source = "chr21.fa"
contaminant = "GCF_000018665.1_ASM1866v1_genomic.fna"

In [273]:
src_genome = parse_fasta(source, READ_LENGTH)
print(len(src_genome))

445378


In [274]:
contaminated_genome = contaminate(src_genome, contaminant)
print(len(contaminated_genome))
write_fasta(filename="contaminated_with_%s"%(contaminant), 
            reads=contaminated_genome, 
            header=CONTAMINANT_HEADER, 
            label='>%s'%(contaminant),
            limit=LINE_LENGTH)

introducing 22268 contaminants from contaminant GCF_000018665.1_ASM1866v1_genomic.fna
467646
writing to contaminated_with_GCF_000018665.1_ASM1866v1_genomic.fna


### Find Unmapped Reads via Alignment with Bowtie2

In [336]:
index = "human21Chrom"
contaminant = "GCF_000018665.1_ASM1866v1_genomic.fna"
contaminated_file = "contaminated_with_%s"%(contaminant)

#### Run Bowtie2 Alignment

In [337]:
process = subprocess.Popen( args=["bowtie2", 
                                  "-x", index, 
                                  "-f", contaminated_file, 
                                  "-S", BOWTIE_ALIGNMENTS_INPUT ] )
process.wait()

0

In [338]:
print("Logging unmapped reads from Bowtie2 alignment of contaminated genome")
with open(BOWTIE_ALIGNMENTS_INPUT, 'r') as fr:
    with open(BOWTIE_UNMAPPED_OUTPUT, 'w') as fw:
        for line in fr:
            values = line.split("\t")
            if len(values) > READ_COL:
                if int(values[UNMAPPED_STATUS_COL]) == UNMAPPED_FLAG:
                    unmapped_read = values[READ_COL]
                    print('unmapped read: %s'%(unmapped_read))
                    fw.write(unmapped_read + "\n")

Logging unmapped reads from Bowtie2 alignment of contaminated genome
unmapped read: AACTAGACTTCGACAATGACAGAGGAACCTACGAACGATGCAGGCCAGGGCCTGTGGCAAGTCTGCGTTGAGCAACTGGGGCAGGAAATG
unmapped read: CCCGAACAGCAGTTCAACACCTGGATCAAGCCCCTGACCGCGCACGTCGCCGAAGACTTCTCCAAAGTCACCGTCTACGTGGCCAACCGC
unmapped read: TTCAAGCTCGACTGGATCCGCGCCCAATATGCAGGCCGCATCTCGGCCATGCTGGAGTCGCTCTATGGCCAGCCGGTGACGCTTGAGTTG
unmapped read: GCACTTGCTCAGCGGGAAAGCGTTGTGCGGACTTACGTCCGCCCCTCCTCCAGCGAGCGCTCGGCCCCACCGGAAACCATCGTCACCTCG
unmapped read: GTGCCCACGGTCACCAGCGAAGACGCGGCAGCGCCCGTCTTTCGCACGCGCCTGAACGCCGCGCTGACCTTCGAGACCCTGGTGGAAGGT
unmapped read: ACGGCCAACCGCATGGCACGCTCGGCCGCCATGCATGTGGCGGGCTCGCCCGGACACCTGTACAACCCGCTGTTCATCTACGGCGGCGTG
unmapped read: GGCCTGGGCAAGACCCACCTGGTGCATGCCGTGGGCAACAAGCTGCTGGCCGACAAGCCCGACGCCAAAGTTCTCTACATCCATGCCGAG
unmapped read: CAGTTCGTCTCGGATGTGGTCAAGGCCTACCAGCGCCGCACCTTTGACGAATTCAAGGAGCGTTACCACTCGCTGGATCTGCTGCTGATC
unmapped read: GACGACGTGCAGTTCTTCGCCAACAAGGACCGCACGCAGGAGGAGTTCTTCAACGCCTTCGAGGCGCT

### Read Unmapped Reads from File

In [339]:
with open(BOWTIE_UNMAPPED_OUTPUT, 'r') as fr:
    unmapped_reads = fr.readlines()
    unmapped_reads = [read.strip() for read in unmapped_reads]
print(unmapped_reads)

['...']


### Generate RNN Predictions for Unmapped Reads

#### Load Trained RNN Model from Disk

In [340]:
all_categories = ['D. acidovorans', 'S. epidermidis', 'W. anomalus']
n_categories = 3
read_length = 90
k = 3
n_kmers = read_length - k + 1

In [341]:
class RNN(nn.Module):
    def __init__(self, input_size, hidden_size, output_size):
        super(RNN, self).__init__()
        self.hidden_size = hidden_size
        self.i2h = nn.Linear(input_size + hidden_size, hidden_size)
        self.i2o = nn.Linear(input_size + hidden_size, output_size)
        self.softmax = nn.LogSoftmax(dim=1)

    def forward(self, input, hidden):
        combined = torch.cat((input, hidden), 1)
        hidden = self.i2h(combined)
        output = self.i2o(combined)
        output = self.softmax(output)
        return output, hidden

    def initHidden(self):
        return torch.zeros(1, self.hidden_size)

In [342]:
def lineToTensor(line):
    tensor = torch.zeros(len(line)-k+1, 1, 100)
    for i in range(len(line)-k+1):
        tensor[i][0] = torch.FloatTensor(mk_model.vector(line[i:i+k].upper()))
    return tensor

def evaluate(line_tensor):
    hidden = rnn.initHidden()
    for i in range(line_tensor.size()[0]):
        output, hidden = rnn(line_tensor[i], hidden)
    return output

def predict(input_line, n_predictions=1):
    with torch.no_grad():
        output = evaluate(lineToTensor(input_line))
        prob = torch.softmax(output, dim=1)
        # Get top N categories
        topv, topi = output.topk(n_predictions, 1, True)
        predictions = []
        for i in range(n_predictions):
            value = topv[0][i].item()
            category_index = topi[0][i].item()
            max_prob = prob[0,category_index].numpy()
            predictions.append((all_categories[category_index], max_prob))
    return predictions

In [343]:
filepath = 'dna2vec/pretrained/dna2vec-20161219-0153-k3to8-100d-10c-29320Mbp-sliding-Xat.w2v'
mk_model = MultiKModel(filepath)

In [344]:
rnn = torch.load('./rnn.pt')
rnn

RNN(
  (i2h): Linear(in_features=275, out_features=175, bias=True)
  (i2o): Linear(in_features=275, out_features=3, bias=True)
  (softmax): LogSoftmax()
)

In [345]:
rnn_pred = defaultdict(list)
for unmapped_read in unmapped_reads:
    category, prob = predict(unmapped_read)[0]
    if prob > RNN_THRESHOLD:
        rnn_pred[unmapped_read].append(category)
for read in rnn_pred:
    max_category = Counter(rnn_pred[read]).most_common(1)[0]
    rnn_pred[read] = max_category[0]

### Generate Sketching (Bloom Filter) Predictions for Unmapped Reads

In [ ]:
overlapped_reads = {}
for unmapped_read in unmapped_reads:
    category = None
    if unmapped_read in rnn_pred and rnn_pred[unmapped_read] == category:
        overlapped_reads[unmapped_read] = category

### Verify Overlapped Predictions with Bowtie2 Alignment

In [346]:
indexes = {}
indexes['D. acidovorans'] = "acidovorans"
indexes['S. epidermidis'] = "epidermidis"
indexes['W. anomalus'] = "anomalus"
mapped = set()

In [347]:
overlapped_reads = rnn_pred

In [348]:
print('predicted set of unmapped reads mapped to contaminant genomes:')
for read in overlapped_reads:
    print('%s introduced by contaminant genome %s'%(read, overlapped_reads[read]))

predicted set of unmapped reads mapped to contaminant genomes:
GATTTACGTCTCTGACCATGGAGAATCACTGGGTGAAAATAACATATATCTTCACGGCCTCCCATACTCAATAGCGCCCAACGTACAGAA introduced by contaminant genome W. anomalus
GCCTGCTGCAGGTGCAGATCGGCGACGCCATCGAGGCCGACCGCGTGTTCACCATGCTCATGGGCGATGAAGTGGAGCCACGCCGGGAAT introduced by contaminant genome W. anomalus
AATCTCGCTTCAAGGAAATTGAATCATGGGTATCAGTAAATGGCTATTTGGAAAAATTCAACATAACAATAATGGTGGCCATCACCAAAA introduced by contaminant genome S. epidermidis
CAACTCGCCCTGCTTGAGCTGGGCATTGGGGTTCTTTTGCTGCAGCTCCTTGGCGATGAAGCGTTCGGTCACCCAGGCGTCCACCCGCTT introduced by contaminant genome D. acidovorans
GCAGCTCGTTGAAGTCCACGCCGCGCCCTTCGAAGGCTTCGCGGCACAGTTGCTCGTCTCCCGTCTGGAAATGGGCGGCGGCAAAGGCGT introduced by contaminant genome D. acidovorans
TTCTCCACCATGGTCATCCCGGCCGGCAATGAAGGCCCCTCGCACCTGCACACCGATGTGGAGGAAGTCTTCTTCCTGATCCGCGGCAAG introduced by contaminant genome W. anomalus
TCGGAAAGCACCCCGCGCGACGTGCAGCAACTGCAGCAGTTGCTGCTGCAGGACCGCGAGCGCGGCTACGCCATGGGCGAGGGCTTCTAC introduced by contami

In [334]:
print("Verifying unmapped reads against contaminant genome with Bowtie2 alignment")
count = 0
reads = []
for read in overlapped_reads:
    reads.append(read)
    index = indexes[overlapped_reads[read]]
    write_fasta(filename=OVERLAP_OUTPUT_FILE, 
                reads=[read], 
                header=OVERLAP_HEADER, 
                label=">%s"%(OVERLAP_OUTPUT_FILE),
                limit=LINE_LENGTH)
    process = subprocess.Popen( args=["bowtie2", 
                                  "-x", index, 
                                  "-f", OVERLAP_OUTPUT_FILE, 
                                  "-S", BOWTIE_ALIGNMENTS_INPUT ] )
    process.wait()
    with open(BOWTIE_ALIGNMENTS_INPUT, 'r') as fr:
        for line in fr:
            values = line.split("\t")
            if len(values) > READ_COL:
                if int(values[UNMAPPED_STATUS_COL]) == MAPPED_FLAG:
                    mapped.add(read)
                    print('%s mapped to %s'%(values[READ_COL], overlapped_reads[read]))
                    break
    count += 1
    if count == ALIGNMENT_VALIDATION_LIMIT:
        break

Verifying unmapped reads against contaminant genome with Bowtie2 alignment
CAACTCGCCCTGCTTGAGCTGGGCATTGGGGTTCTTTTGCTGCAGCTCCTTGGCGATGAAGCGTTCGGTCACCCAGGCGTCCACCCGCT mapped to D. acidovorans
GCAGCTCGTTGAAGTCCACGCCGCGCCCTTCGAAGGCTTCGCGGCACAGTTGCTCGTCTCCCGTCTGGAAATGGGCGGCGGCAAAGGCG mapped to D. acidovorans
GCGCAGCGTGTTGAAAGTGCCGATCAGGTTCACGCGCACGATGCCCGTGTACTTGTCCAGCGAGCCGGGGCTGCCGTCCTTTTCCACCA mapped to D. acidovorans
TTGGGCAGGGTGCCCGGCAGCACCATCTGCACATCGCCGCGCAGCTTGGTGACTTCGCGCACGGCATCGGACAGTTGCTGGGCCAGGCC mapped to D. acidovorans
GGCCATGGCGCTCAATGCCGTGGCCATGAACGCCTCGCGCATCATCGGCCCGCTGGTGGCCGGCGCCATCATCGCCAGCCTGGGCAGCG mapped to D. acidovorans
ACCATGGACTCCTCCGAGATCTCCAGCGTGCGTGCCGAGCACGCCAAGTCCCAGGCCGCGCTGCTGCACGCGCGCCAGGAATTCGACCG mapped to D. acidovorans
TCGGCGCAGAACCATTCGGCCTGCAGCTCCTCGGTGTCGGCGCGGATGGCGGCCAGCGCCAGGTCGGCCTGGCCCGAGGCCACCTGGGC mapped to D. acidovorans
GGCAGGGCCATGGCTGCAGGTCGATCGCCGCAGCAAGCGTGTTCAGCGCGAGGCGCGCAGCACCACGCCGTCCAGCGAAGGCGCATGCA mapped to D. acidovorans
CAGGC

In [335]:
aligned = 0
for read in reads:
    if read in mapped:
        aligned += 1
print("%d/%d of the first %d unmapped reads generated from a contaminant genome"%(aligned, len(reads), len(reads)))

532/1000 of the first 1000 unmapped reads generated from a contaminant genome
